In [1]:
def draw_cortex_vertex(subject,data,cmap,vmin,vmax,cbar = 'discrete',cmap_steps = 255,\
                        alpha = None,depth = 1,thick = 1,height = 1024,sampler = 'nearest',\
                        with_curvature = True,with_labels = False,with_colorbar = False,\
                        with_borders = False,curv_brightness = 0.95,curv_contrast = 0.05,add_roi = False,\
                        roi_name = 'empty',col_offset = 0, zoom_roi = None, zoom_hem = None, zoom_margin = 0.0):
    """
    Plot brain data onto a previously saved flatmap.

    Parameters
    ----------
    subject             : subject id (e.g. 'sub-001')
    data                : the data you would like to plot on a flatmap
    cmap                : colormap that shoudl be used for plotting
    vmin                : minimal value iqn colormap
    vmax                : maximal value in colormap
    cbar                : color bar layout
    cmap_steps          : number of colormap bins
    alpha               : alpha map
    depth               : Value between 0 and 1 for how deep to sample the surface for the flatmap (0 = gray/white matter boundary, 1 = pial surface)
    thick               : Number of layers through the cortical sheet to sample. Only applies for pixelwise = True
    height              : Height of the image to render. Automatically scales the width for the aspect of the subject's flatmap
    sampler             : Name of sampling function used to sample underlying volume data. Options include 'trilinear', 'nearest', 'lanczos'
    with_curvature      : Display the rois, labels, colorbar, annotated flatmap borders, or cross-hatch dropout?
    with_labels         : Display labels?
    with_colorbar       : Display pycortex' colorbar?
    with_borders        : Display borders?
    curv_brightness     : Mean brightness of background. 0 = black, 1 = white, intermediate values are corresponding grayscale values.
    curv_contrast       : Contrast of curvature. 1 = maximal contrast (black/white), 0 = no contrast (solid color for curvature equal to curvature_brightness).
    add_roi             : add roi -image- to overlay.svg
    roi_name            : roi name
    col_offset          : colormap offset between 0 and 1
    zoom_roi            : name of the roi on which to zoom on
    zoom_hem            : hemifield fo the roi zoom
    zoom_margin         : margin in mm around the zoom

    Returns
    -------
    vertex_rgb - pycortex vertex file
    """
    
    import cortex
    import pdb
    import numpy as np
    import matplotlib.pyplot as plt
    import matplotlib.colors as colors
    from matplotlib import cm
    import matplotlib as mpl
    import matplotlib.pyplot as pl
    import ipdb
    deb = ipdb.set_trace

    # define colormap
    base = cortex.utils.get_cmap(cmap)
    val = np.fmod(np.linspace(0+col_offset, 1+col_offset,cmap_steps+1,endpoint=False),1.0)
    colmap = colors.LinearSegmentedColormap.from_list(  'my_colmap',
                                                        base(val),
                                                        N = cmap_steps)

    # convert data to RGB
    vrange = float(vmax) - float(vmin)
    norm_data = ((data-float(vmin))/vrange)*cmap_steps
    mat = colmap(norm_data.astype(int))

    vertex_rgb = cortex.VertexRGB(  red = mat[...,0],
                                    green = mat[...,1],
                                    blue = mat[...,2],
                                    alpha = alpha,
                                    subject = subject,
                                    )
    
    vertex_rgb_fig = cortex.quickshow(  braindata = vertex_rgb,
                                        depth = depth,
                                        thick = thick,
                                        height = height,
                                        sampler = sampler,
                                        with_curvature = with_curvature,
                                        with_labels = with_labels,
                                        with_colorbar = with_colorbar,
                                        with_borders = with_borders,
                                        curvature_brightness = curv_brightness,
                                        curvature_contrast = curv_contrast)
    
    zoom_plot = []
    if zoom_roi != None:
        roi_verts = cortex.get_roi_verts(subject, zoom_roi)[zoom_roi]
        roi_map = cortex.Vertex.empty(subject)
        roi_map.data[roi_verts] = 1

        (lflatpts, lpolys), (rflatpts, rpolys) = cortex.db.get_surf(subject, "flat", nudge=True)
        sel_pts = dict(left=lflatpts, right=rflatpts)[zoom_hem]
        roi_pts = sel_pts[np.nonzero(getattr(roi_map, zoom_hem))[0],:2]
        
        xmin, ymin = roi_pts.min(0) - zoom_margin
        xmax, ymax = roi_pts.max(0) + zoom_margin
        zoom_width = roi_pts.max(0)[0]- roi_pts.min(0)[0]
        zoom_height = roi_pts.max(0)[1]- roi_pts.min(0)[1]
        sqr_zoom_size = np.round(np.max([zoom_width,zoom_height]))*1.1
        zoom_ctr_x = np.mean([roi_pts.max(0)[0],roi_pts.min(0)[0]])
        zoom_ctr_y = np.mean([roi_pts.max(0)[1],roi_pts.min(0)[1]])
        mat = [zoom_ctr_x-sqr_zoom_size/2.0,zoom_ctr_x+sqr_zoom_size/2.0,zoom_ctr_y-sqr_zoom_size/2.0,zoom_ctr_y+sqr_zoom_size/2.0]
        zoom_plot = pl.axis(mat)
    else:
        
        if cbar == 'polar':

            # Polar angle color bar
            colorbar_location = [0.5, 0.07, 0.8, 0.2]
            n = 200
            cbar_axis = vertex_rgb_fig.add_axes(colorbar_location, projection='polar')
            norm = mpl.colors.Normalize(0, 2*np.pi)

            # Plot a color mesh on the polar plot
            # with the color set by the angle
            t = np.linspace(2*np.pi,0,n)
            r = np.linspace(1,0,2)
            rg, tg = np.meshgrid(r,t)
            c = tg
            im = cbar_axis.pcolormesh(t, r, c.T,norm= norm, cmap = colmap)
            cbar_axis.set_theta_zero_location("W")
            cbar_axis.set_yticklabels([])
            cbar_axis.set_xticklabels([])
            cbar_axis.spines['polar'].set_visible(False)

        elif cbar == 'ecc':
        
            # Ecc color bar
            colorbar_location = [0.5, 0.07, 0.8, 0.2]
            n = 200
            cbar_axis = vertex_rgb_fig.add_axes(colorbar_location, projection='polar')

            t = np.linspace(0,2*np.pi, n)
            r = np.linspace(0,1, n)
            rg, tg = np.meshgrid(r,t)
            c = tg
            
            im = cbar_axis.pcolormesh(t, r, c, norm = mpl.colors.Normalize(0, 2*np.pi), cmap = colmap)
            cbar_axis.tick_params(pad = 1,labelsize = 15)
            cbar_axis.spines['polar'].set_visible(False)
            
            # superimpose new axis for dva labeling
            box = cbar_axis.get_position()
            cbar_axis.set_yticklabels([])
            cbar_axis.set_xticklabels([])
            axl = vertex_rgb_fig.add_axes(  [1.8*box.xmin,
                                        0.5*(box.ymin+box.ymax),
                                        box.width/600,
                                        box.height*0.5],
                                        axisbg = None)
            axl.spines['top'].set_visible(False)
            axl.spines['right'].set_visible(False)
            axl.spines['bottom'].set_visible(False)
            axl.yaxis.set_ticks_position('right')
            axl.xaxis.set_ticks_position('none')
            axl.set_xticklabels([])
            axl.set_yticklabels(np.linspace(vmin,vmax,3),size = 'x-large')
            axl.set_ylabel('$dva$\t\t', rotation = 0, size = 'x-large')
            axl.yaxis.set_label_coords(box.xmax+30,0.4)
            axl.patch.set_alpha(0.5)

        elif cbar == 'discrete':

            # Discrete color bars
            # -------------------
            colorbar_location= [0.9, 0.05, 0.03, 0.25]
            cmaplist = [colmap(i) for i in range(colmap.N)]

            # define the bins and normalize
            bounds = np.linspace(vmin, vmax, cmap_steps + 1)
            bounds_label = np.linspace(vmin, vmax, 3)
            norm = mpl.colors.BoundaryNorm(bounds, colmap.N)
            
            cbar_axis = vertex_rgb_fig.add_axes(colorbar_location)
            cb = mpl.colorbar.ColorbarBase(cbar_axis,cmap = colmap,norm = norm,ticks = bounds_label,boundaries = bounds)

        # add to overalt
        if add_roi == True:
            cortex.utils.add_roi(   data = vertex_rgb,
                                    name = roi_name,
                                    open_inkscape = False,
                                    add_path = False,
                                    depth = depth,
                                    thick = thick,
                                    sampler = sampler,
                                    with_curvature = with_curvature,
                                    with_colorbar = with_colorbar,
                                    with_borders = with_borders,
                                    curvature_brightness = curv_brightness,
                                    curvature_contrast = curv_contrast)

    return vertex_rgb

def rotate_pts(pts,orig,rot_deg):
    """
    -----------------------------------------------------------------------------------------
    rotate_pts(pts,orig,rot_deg)
    -----------------------------------------------------------------------------------------
    Goal of the script:
    rotate pts aroud an origin
    -----------------------------------------------------------------------------------------
    Input(s):
    pts: coordinates to rotate
    rot_deg: rotation amount
    -----------------------------------------------------------------------------------------
    Output(s):
    rot_pts: rotated points
    -----------------------------------------------------------------------------------------
    """
    rot = np.radians(rot_deg)
    qx = orig[0] + np.cos(rot) * (pts[0] - orig[0]) + np.sin(rot) * (pts[1] - orig[1])
    qy = orig[1] + -np.sin(rot) * (pts[0] - orig[0]) + np.cos(rot) * (pts[1] - orig[1])
    rot_pts = [qx,qy]
    return rot_pts

def rot_coord(coord,rot_deg):
    """
    -----------------------------------------------------------------------------------------
    rot_coord(coord,rot_deg)
    -----------------------------------------------------------------------------------------
    Goal of the script:
    Rotate complex numbers with rotation matrix
    -----------------------------------------------------------------------------------------
    Input(s):
    coord: complex numbers coordinate set
    rot_deg: rotation in degrees
    -----------------------------------------------------------------------------------------
    Output(s):
    coord_rot: rotated coordinates
    -----------------------------------------------------------------------------------------
    """
    theta = np.radians(rot_deg)
    c, s = np.cos(theta), np.sin(theta)
    R = np.matrix([[c, -s], [s, c]])
    coord_rot = np.array(np.dot(coord,R))
    
    return coord_rot

def get_colors(data,cmap,cmap_steps,col_offset,vmin,vmax):
    """
    -----------------------------------------------------------------------------------------
    get_colors(data,cmap,cmap_steps,col_offset,vmin,vmax)
    -----------------------------------------------------------------------------------------
    Goal of the script:
    Return for a given dataset the corresponding colors in Bokeh
    -----------------------------------------------------------------------------------------
    Input(s):
    data: data from which to get colors on colormaps
    cmap: colromap
    cmpas: steps for the colormap
    col_offset: color offset on the colormap scale
    vmin: minimum corresponding value on the colormap
    vmax: maximum corresponding value on the colormap
    -----------------------------------------------------------------------------------------
    Output(s):
    colors_val_rgb: matrix of colors for bokeh
    -----------------------------------------------------------------------------------------
    """
    import matplotlib.colors as colors
    base = cortex.utils.get_cmap(cmap)
    val = np.fmod(np.linspace(0 + col_offset, 1 + col_offset, cmap_steps + 1, endpoint = False), 1.0)
    colmap = colors.LinearSegmentedColormap.from_list('my_colmap', base(val), N = cmap_steps)
    vrange = float(vmax) - float(vmin)
    norm_data = (( data - float(vmin) ) / vrange) * cmap_steps 
    col_mat_rgb = colmap(norm_data.astype(int)) * 255.0
    colors_val_rgb = ["#%02x%02x%02x" % (int(r), int(g), int(b)) for r, g, b in zip(col_mat_rgb[:,0], col_mat_rgb[:,1], col_mat_rgb[:,2])]
    return colors_val_rgb

def roi_coord_mask(roi,hem,subject = 'fsaverage'):
    """
    -----------------------------------------------------------------------------------------
    roi_coord_mask(roi,hem,subject = 'fsaverage')
    -----------------------------------------------------------------------------------------
    Goal of the script:
    Ger ROI pts coordinates and mask
    -----------------------------------------------------------------------------------------
    Input(s):
    subject: subject name
    roi: roi name
    hem: hemifield
    margin: mm out of ROI
    -----------------------------------------------------------------------------------------
    Output(s):
    roi_pts: pts coordinates on flat map
    roi_mask: roi mask
    -----------------------------------------------------------------------------------------
    """

    # get data
    roi_verts = cortex.get_roi_verts(subject, roi)[roi]
    roi_map = cortex.Vertex.empty(subject)
    roi_map.data[roi_verts] = 1
    (lflatpts, lpolys), (rflatpts, rpolys) = cortex.db.get_surf(subject, "flat",nudge=True)
    sel_pts = dict(left=lflatpts, right=rflatpts)[hem]
    roi_pts = sel_pts[np.nonzero(getattr(roi_map, hem))[0],:2]
    if hem == 'left':
        roi_mask = np.hstack([roi_map.left[:],roi_map.right[:]*0])
    elif hem == 'right':
        roi_mask = np.hstack([roi_map.left[:]*0,roi_map.right[:]])
    roi_mask = roi_mask==1
    
    return(roi_pts,roi_mask)


In [20]:
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))

# Stop warnings
# -------------
import warnings
warnings.filterwarnings("ignore")

# General imports
# ---------------
import os
import sys
import json
import glob
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.colors as colors
import matplotlib.colors as colors
import ipdb
import platform
import wquantiles
opj = os.path.join
deb = ipdb.set_trace

%matplotlib inline

# MRI imports
# -----------
import nibabel as nb
import cortex

# Bokeh import
# ------------
from bokeh.plotting import figure 
from bokeh.models import ColumnDataSource
from bokeh.models.tools import HoverTool
from bokeh.models.annotations import Span, Label
from bokeh.layouts import row, column, gridplot
from bokeh.models import BoxZoomTool, BoxSelectTool, Spacer, WheelZoomTool, PanTool, ResetTool
from bokeh.models.glyphs import Text
from bokeh.models.mappers import LinearColorMapper
from bokeh.io import output_notebook, show,save, output_file, export_png, export_svgs
from bokeh.models import Arrow, OpenHead, NormalHead, VeeHead
import matplotlib.image as mpimg
output_notebook()
# Settings
# --------
subject = '999999'
fit_model = 'gauss'
save_svg = 1
rot_left = 10
rot_right = 20
nbins = 20
small_size_dot = 5
big_size_dot = small_size_dot*3

# Define analysis parameters
# --------------------------
with open('../../settings.json') as f:
    json_s = f.read()
    analysis_info = json.loads(json_s)

# Define cluster/server specific parameters
# -----------------------------------------
if 'aeneas' in platform.uname()[1]:
    base_dir = analysis_info['aeneas_base_folder']
    main_cmd = '/home/szinte/software/workbench/bin_rh_linux64/wb_command'
elif 'local' in platform.uname()[1]:
    base_dir = analysis_info['local_base_folder']
    main_cmd = '/Applications/workbench/bin_macosx64/wb_command'

deriv_dir = opj(base_dir,'pp_data',subject,fit_model,'deriv')
if save_svg == 1:
    svg_folder = opj(base_dir,"pp_data",subject,fit_model,"figs","svg","neg","LR","ANG_LR_neg_pRFecc_prog")
    try: os.makedirs(svg_folder)
    except: pass


Loading BokehJS ...

In [21]:
# Create derivatives flatmaps
# ---------------------------
roi = 'ANG'
cmap_ecc_size = 'Spectral'
sign_idx, rsq_idx, ecc_idx, polar_real_idx, polar_imag_idx , size_idx, \
            non_lin_idx, amp_idx, baseline_idx, cov_idx, x_idx, y_idx = 0,1,2,3,4,5,6,7,8,9,10,11
mask_dir  = 'neg'
ecc_vmin = 0
ecc_vmax = 8

# Get data and combine hemispheres
deriv_mat=[]
for hemi in ['L','R']:
    deriv_file = nb.load(opj(deriv_dir,mask_dir,"prf_deriv_{hemi}_{mask_dir}_fsaverage.func.gii".format(hemi = hemi, mask_dir = mask_dir)))
    deriv_mat.append(np.array([deriv_file.darrays[i].data for i in range(len(deriv_file.darrays))]))
deriv_mat = np.hstack(deriv_mat)
deriv_mat = deriv_mat.T
threshold_mask = np.logical_and(np.logical_and( deriv_mat[:,rsq_idx]>=0.0,
                                                deriv_mat[:,ecc_idx]<=8.0),
                                                deriv_mat[:,size_idx]>=0.1)

In [22]:
# R-square
rsq_data = deriv_mat[:,rsq_idx]
rsq_data[~threshold_mask] = np.nan
alpha = rsq_data

# Eccentricity
ecc_data = deriv_mat[:,ecc_idx]
ecc_data[~threshold_mask] = np.nan

param_ecc = {'data': ecc_data.T, 'cmap': cmap_ecc_size, 'alpha': alpha.T, 'vmin': ecc_vmin, 'vmax': ecc_vmax, 'cbar': 'ecc',
            'curv_brightness': 0.05, 'curv_contrast': 0.1, 
            'subject': 'fsaverage','add_roi': False, 'zoom_roi': 'ANG', 'zoom_hem': 'left', 'zoom_margin': 1.0}

vertex_ecc = draw_cortex_vertex(**param_ecc)

plt.savefig(opj(svg_folder,'ANG_left_ecc.png'),bbox_inches = 'tight')
plt.savefig(opj(svg_folder,'ANG_left_ecc.pdf'),bbox_inches = 'tight')
plt.close()

param_ecc = {'data': ecc_data.T, 'cmap': cmap_ecc_size, 'alpha': alpha.T, 'vmin': ecc_vmin, 'vmax': ecc_vmax,'cbar': 'ecc',
            'curv_brightness': 0.05, 'curv_contrast': 0.1,
            'subject': 'fsaverage','add_roi': False, 'zoom_roi': 'ANG', 'zoom_hem': 'right', 'zoom_margin': 1.0}

vertex_ecc = draw_cortex_vertex(**param_ecc)
plt.savefig(opj(svg_folder,'ANG_right_ecc.png'),bbox_inches = 'tight')
plt.savefig(opj(svg_folder,'ANG_right_ecc.pdf'),bbox_inches = 'tight')
plt.close()

In [23]:
# -----------------
# Zoom ROI in bokeh
# -----------------

# Settings
arrow_start = [0.5,0.2]
arrow_end = [0.5,0.8]
arrow_ctr = [0.5,0.5]
p_width = 400
p_height = 400
min_border_large = 10
stim_color = tuple([250,250,250])
bg_color = tuple([229,229,229])
valtick = (np.linspace(0,1,11))

x_range_zoom = (0,1)
y_range_zoom = (0,1)
x_label_zoom = 'ROI short axis (norm.)'
y_label_zoom = 'ROI long axis (norm.)'

# Load images
left_filename = opj(svg_folder,'ANG_left_ecc.png')
img_left = mpimg.imread(left_filename)
img_left = img_left*255.0
img_left = np.flipud(img_left)
right_filename = opj(svg_folder,'ANG_right_ecc.png')
img_right = mpimg.imread(right_filename)
img_right = img_right*255.0
img_right = np.flipud(img_right)

# Left ANG
# --------
# Define figure
zoom_left = figure( plot_width = p_width,
                    plot_height = p_height,
                    x_range = x_range_zoom,
                    y_range = y_range_zoom,
                    min_border_left = min_border_large,
                    min_border_right = min_border_large,
                    min_border_bottom = min_border_large,
                    min_border_top = min_border_large,
                    toolbar_location = None,
                    title = '')

zoom_left.xaxis.axis_label = x_label_zoom
zoom_left.yaxis.axis_label = y_label_zoom
zoom_left.grid.grid_line_color = None
zoom_left.axis.minor_tick_in = False
zoom_left.axis.minor_tick_out = False
zoom_left.axis.major_tick_in = False
zoom_left.outline_line_alpha = 0
xaxis_ticker = np.linspace(0.075,0.95,10)
zoom_left.xaxis.ticker = xaxis_ticker

dict_label = {}
for val_num, val in enumerate(xaxis_ticker):
    dict_label.update({val: '%1.0g'%valtick[val_num]})
zoom_left.xaxis.ticker = xaxis_ticker    
zoom_left.xaxis.major_label_overrides = dict_label
yaxis_ticker = np.linspace(0.025,0.975,11)
valtick = (np.linspace(0,1,11))
dict_label = {}
for val_num, val in enumerate(yaxis_ticker):
    dict_label.update({val: '%1.0g'%valtick[val_num]})
zoom_left.yaxis.ticker = yaxis_ticker    
zoom_left.yaxis.major_label_overrides = dict_label
zoom_left.background_fill_color = bg_color
zoom_left.axis.axis_label_standoff = 10
zoom_left.axis.axis_label_text_font_style = 'normal'

# Draw roi
zoom_left.image_rgba(image=[img_left.astype('uint8')], x=-0.05, y=-0.06, dw=1.1,dh=1.1)

# Draw arrow
arrow_start_left = rotate_pts(arrow_start,arrow_ctr,-rot_left)
arrow_end_left = rotate_pts(arrow_end,arrow_ctr,-rot_left)
zoom_left.add_layout(Arrow(end = NormalHead(size = 10,fill_color = 'black', line_color = 'black',line_width = 6), 
                            x_start = arrow_start_left[0], y_start = arrow_start_left[1],
                            x_end = arrow_end_left[0], y_end = arrow_end_left[1], line_color = 'black',line_width = 6))
zoom_left.add_layout(Arrow(end = NormalHead(size = 10,fill_color = 'white', line_color= 'white',line_width = 2), 
                            x_start = arrow_start_left[0], y_start = arrow_start_left[1],
                            x_end = arrow_end_left[0], y_end = arrow_end_left[1],line_color = 'white',line_width = 2))

# Draw title
zoom_left.text(x = 0.05, y = 0.95, text = ['ANG LH'],text_color = 'white',text_font_size = '10pt', text_align = 'left', text_baseline = 'middle')

# Right ANG
# ---------
# Define figure
zoom_right = figure(plot_width = p_width,
                    plot_height = p_height,
                    x_range = x_range_zoom,
                    y_range = y_range_zoom,
                    min_border_left = min_border_large,
                    min_border_right = min_border_large,
                    min_border_bottom = min_border_large,
                    min_border_top = min_border_large,
                    toolbar_location = None,
                    title = '')

zoom_right.xaxis.axis_label = x_label_zoom
zoom_right.yaxis.axis_label = y_label_zoom
zoom_right.grid.grid_line_color = None
zoom_right.axis.minor_tick_in = False
zoom_right.axis.minor_tick_out = False
zoom_right.axis.major_tick_in = False
zoom_right.outline_line_alpha = 0

xaxis_ticker = np.linspace(0.18,0.85,11)
zoom_right.xaxis.ticker = xaxis_ticker
dict_label = {}
for val_num, val in enumerate(xaxis_ticker):
    dict_label.update({val: '%1.0g'%valtick[val_num]})
zoom_right.xaxis.ticker = xaxis_ticker    
zoom_right.xaxis.major_label_overrides = dict_label
yaxis_ticker = np.linspace(0.025,0.975,11)
valtick = (np.linspace(0,1,11))
dict_label = {}
for val_num, val in enumerate(yaxis_ticker):
    dict_label.update({val: '%1.0g'%valtick[val_num]})
zoom_right.yaxis.ticker = yaxis_ticker    
zoom_right.yaxis.major_label_overrides = dict_label
zoom_right.background_fill_color = bg_color
zoom_right.axis.axis_label_standoff = 10
zoom_right.axis.axis_label_text_font_style = 'normal'

# Draw roi
zoom_right.image_rgba(image=[img_right.astype('uint8')], x=-0.05, y=-0.06, dw=1.1,dh=1.1)

# Draw arrow
arrow_start_right = rotate_pts(arrow_start,arrow_ctr,-rot_right)
arrow_end_right = rotate_pts(arrow_end,arrow_ctr,-rot_right)
zoom_right.add_layout(Arrow(end = NormalHead(size = 10,fill_color = 'black', line_color= 'black',line_width=6), 
                            x_start = arrow_start_right[0], y_start = arrow_start_right[1],
                            x_end = arrow_end_right[0], y_end = arrow_end_right[1],line_color = 'black',line_width=6))
zoom_right.add_layout(Arrow(end = NormalHead(size = 10,fill_color = 'white', line_color= 'white',line_width=2), 
                            x_start = arrow_start_right[0], y_start = arrow_start_right[1],
                            x_end = arrow_end_right[0], y_end = arrow_end_right[1],line_color = 'white',line_width=2))

# Draw title
zoom_right.text(x = 0.05, y = 0.95, text = ['ANG RH'],text_color = 'white',text_font_size = '10pt', text_align = 'left', text_baseline = 'middle')

GlyphRenderer(id='c16fbf43-a8ef-424c-976e-d17d9f70c87f', ...)

In [24]:
# ROI rotation
# ------------
# define left coordinates
ang_coord_left, ang_mask_left = roi_coord_mask('ANG','left')
alpha_left = alpha[ang_mask_left]
ecc_left = ecc_data[ang_mask_left]
ecc_left = ecc_left[~np.isnan(alpha_left)]
ecc_col_left = get_colors(ecc_left, cmap_ecc_size, 255, 0.0, ecc_vmin, ecc_vmax)
ang_coord_left = ang_coord_left[~np.isnan(alpha_left)]
ang_coord_rot_left = rot_coord(ang_coord_left,rot_left)
alpha_left = alpha_left[~np.isnan(alpha_left)]

# define right coordinates
ang_coord_right, ang_mask_right = roi_coord_mask('ANG','right')
alpha_right = alpha[ang_mask_right]
ecc_right = ecc_data[ang_mask_right]
ecc_right = ecc_right[~np.isnan(alpha_right)]
ecc_col_right = get_colors(ecc_right, cmap_ecc_size, 255, 0.0, ecc_vmin, ecc_vmax)
ang_coord_right = ang_coord_right[~np.isnan(alpha_right)]
ang_coord_rot_right = rot_coord(ang_coord_right,rot_right)
alpha_right = alpha_right[~np.isnan(alpha_right)]

In [25]:
# Eccentricity progression computation
# ------------------------------------

# ANG Left
# --------
# Rename values
roi_long_left = ang_coord_rot_left[:,1]
weights_left = alpha_left

# Define value for scatter plot
scatter_roi_long_left_norm = (roi_long_left - np.min(roi_long_left))/(np.max(roi_long_left)-np.min(roi_long_left))
scatter_ecc_left = ecc_left
scatter_ecc_left_col = ecc_col_left
scatter_rsq_left_norm = (weights_left - np.min(weights_left))/(np.max(weights_left)-np.min(weights_left))
scatter_size_dots_left = np.round(small_size_dot+scatter_rsq_left_norm*big_size_dot)

# Define binned values
bin_left = np.zeros(nbins+1)
roi_long_axis = np.linspace(0,1,nbins+1)
for tbin,bin_val in enumerate(roi_long_axis):
    bin_left[tbin] = wquantiles.quantile(data = roi_long_left, weights = weights_left, quantile = bin_val)

bin_rsq_left, bin_roi_long_left, bin_ecc_left = np.zeros(nbins), np.zeros(nbins), np.zeros(nbins)
for bin_left_num in np.arange(0,nbins,1):
    val2pick = np.logical_and(roi_long_left >= bin_left[bin_left_num],roi_long_left <= bin_left[bin_left_num+1])
    # Average
    bin_ecc_left[bin_left_num] = np.average(a = ecc_left[val2pick],weights = weights_left[val2pick])
    bin_rsq_left[bin_left_num] = np.average(a = weights_left[val2pick],weights = weights_left[val2pick])
    bin_roi_long_left[bin_left_num] = np.average(a = roi_long_left[val2pick], weights = weights_left[val2pick])
    
# Normalization
bin_ecc_left_col = get_colors(bin_ecc_left, cmap_ecc_size, 255, 0.0, ecc_vmin, ecc_vmax)
bin_rsq_left_norm = (bin_rsq_left - np.min(bin_rsq_left))/(np.max(bin_rsq_left)-np.min(bin_rsq_left))
bin_size_dots_left = np.round(small_size_dot+bin_rsq_left_norm*big_size_dot)
bin_roi_long_left_norm = (bin_roi_long_left - np.min(roi_long_left))/(np.max(roi_long_left)-np.min(roi_long_left))

In [26]:
# ANG right
# ---------
# Rename values
roi_long_right = ang_coord_rot_right[:,1]
weights_right = alpha_right

# Define value for scatter plot
scatter_roi_long_right_norm = (roi_long_right - np.min(roi_long_right))/(np.max(roi_long_right)-np.min(roi_long_right))
scatter_ecc_right = ecc_right
scatter_ecc_right_col = ecc_col_right
scatter_rsq_right_norm = (weights_right - np.min(weights_right))/(np.max(weights_right)-np.min(weights_right))
scatter_size_dots_right = np.round(small_size_dot+scatter_rsq_right_norm*big_size_dot)

# Define binned values
bin_right = np.zeros(nbins+1)
roi_long_axis = np.linspace(0,1,nbins+1)
for tbin,bin_val in enumerate(roi_long_axis):
    bin_right[tbin] = wquantiles.quantile(data = roi_long_right, weights = weights_right, quantile = bin_val)

bin_rsq_right, bin_roi_long_right, bin_ecc_right = np.zeros(nbins), np.zeros(nbins), np.zeros(nbins)
for bin_right_num in np.arange(0,nbins,1):
    val2pick = np.logical_and(roi_long_right >= bin_right[bin_right_num],roi_long_right <= bin_right[bin_right_num+1])
    # Average
    bin_ecc_right[bin_right_num] = np.average(a = ecc_right[val2pick],weights = weights_right[val2pick])
    bin_rsq_right[bin_right_num] = np.average(a = weights_right[val2pick],weights = weights_right[val2pick])
    bin_roi_long_right[bin_right_num] = np.average(a = roi_long_right[val2pick], weights = weights_right[val2pick])
    
# Normalization
bin_ecc_right_col = get_colors(bin_ecc_right, cmap_ecc_size, 255, 0.0, ecc_vmin, ecc_vmax)
bin_rsq_right_norm = (bin_rsq_right - np.min(bin_rsq_right))/(np.max(bin_rsq_right)-np.min(bin_rsq_right))
bin_size_dots_right = np.round(small_size_dot+bin_rsq_right_norm*big_size_dot)
bin_roi_long_right_norm = (bin_roi_long_right - np.min(roi_long_right))/(np.max(roi_long_right)-np.min(roi_long_right))

In [27]:
# --------
# Drawings
# --------

# General settings
x_range_pp = (0,1)
x_axis_ticker = np.linspace(x_range_pp[0],x_range_pp[1],11)
x_label_pp = 'Main direction (norm.)'
y_range_pp = (-1, 9)
y_axis_ticker = np.linspace(y_range_pp[0],y_range_pp[1],11)
y_label_pp = 'Eccentricity (deg)'

# Define ANG polar progression figure
pp_left = figure(   plot_width = p_width, plot_height = p_height, x_range = x_range_pp, y_range = y_range_pp, min_border_left = min_border_large, min_border_right = min_border_large,
                    min_border_bottom = min_border_large, min_border_top = min_border_large, toolbar_location = None, title = '')

pp_left.xaxis.axis_label = x_label_pp
pp_left.yaxis.axis_label = y_label_pp
pp_left.grid.grid_line_color = None
pp_left.axis.minor_tick_in = False
pp_left.axis.minor_tick_out = False
pp_left.axis.major_tick_in = False
pp_left.outline_line_alpha = 0
pp_left.xaxis.ticker = x_axis_ticker
pp_left.yaxis.ticker = y_axis_ticker
pp_left.background_fill_color = bg_color
pp_left.axis.axis_label_standoff = 10
pp_left.axis.axis_label_text_font_style = 'normal'

# Plot values
pp_left.circle(x = scatter_roi_long_left_norm, y = scatter_ecc_left, line_color = scatter_ecc_left_col,line_alpha = 0.5,fill_color = None,size = scatter_size_dots_left,line_width = 0.5)
pp_left.line(x = bin_roi_long_left_norm, y = bin_ecc_left, color = 'black',line_width = 1)
pp_left.circle(x = bin_roi_long_left_norm, y = bin_ecc_left, line_color = 'black',fill_color = bin_ecc_left_col,size = bin_size_dots_left,line_width = 1)

# Define ANG eccentricity progression figure
pp_right = figure(  plot_width = p_width, plot_height = p_height, x_range = x_range_pp, y_range = y_range_pp, min_border_left = min_border_large, min_border_right = min_border_large,
                    min_border_bottom = min_border_large, min_border_top = min_border_large, toolbar_location = None, title = '')

pp_right.xaxis.axis_label = x_label_pp
pp_right.yaxis.axis_label = y_label_pp
pp_right.grid.grid_line_color = None
pp_right.axis.minor_tick_in = False
pp_right.axis.minor_tick_out = False
pp_right.axis.major_tick_in = False
pp_right.outline_line_alpha = 0
pp_right.xaxis.ticker = x_axis_ticker
pp_right.yaxis.ticker = y_axis_ticker
pp_right.background_fill_color = bg_color
pp_right.axis.axis_label_standoff = 10
pp_right.axis.axis_label_text_font_style = 'normal'

# Plot values
pp_right.circle(x = scatter_roi_long_right_norm, y = scatter_ecc_right, line_color = scatter_ecc_right_col,line_alpha = 0.5,fill_color = None,size = scatter_size_dots_right,line_width = 0.5)
pp_right.line(x = bin_roi_long_right_norm, y = bin_ecc_right, color = 'black',line_width = 1)
pp_right.circle(x = bin_roi_long_right_norm, y = bin_ecc_right, line_color = 'black',fill_color = bin_ecc_right_col,size = bin_size_dots_right,line_width = 1)
f = column(row(zoom_left,pp_left),row(zoom_right,pp_right))

In [28]:
show(f)